# Using external methods for candidate generation in Ax

Out of the box, Ax offers many options for candidate generation, most of which utilize Bayesian optimization algorithms built using [BoTorch](https://botorch.org/). For users that want to leverage Ax for experiment orchestration (via `AxClient` or `Scheduler`) and other features (e.g., early stopping), while relying on other methods for candidate generation, we introduced `ExternalGenerationNode`. 

A `GenerationNode` is a building block of a `GenerationStrategy`. They can be combined together utilize different methods for generating candidates at different stages of an experiment. `ExternalGenerationNode` exposes a lightweight interface to allow the users to easily integrate their methods into Ax, and use them as standalone or with other `GenerationNode`s in a `GenerationStrategy`.

In this tutorial, we will implement a simple generation node using `RandomForestRegressor` from sklearn, and combine it with Sobol (for initialization) to optimize the Hartmann6 problem.

NOTE: This is for illustration purposes only. We do not recommend using this strategy as it typically does not perform well compared to Ax's default algorithms due to it's overly greedy behavior.

In [1]:
import time
from typing import Any, Dict, List, Optional, Tuple

import numpy as np
from ax.core.base_trial import TrialStatus
from ax.core.data import Data
from ax.core.experiment import Experiment
from ax.core.parameter import RangeParameter
from ax.core.types import TParameterization
from ax.modelbridge.external_generation_node import ExternalGenerationNode
from ax.modelbridge.generation_node import GenerationNode
from ax.modelbridge.generation_strategy import GenerationStrategy
from ax.modelbridge.model_spec import ModelSpec
from ax.modelbridge.registry import Models
from ax.modelbridge.transition_criterion import MaxTrials
from ax.plot.trace import plot_objective_value_vs_trial_index
from ax.service.ax_client import AxClient, ObjectiveProperties
from ax.service.utils.report_utils import exp_to_df
from ax.utils.measurement.synthetic_functions import hartmann6
from sklearn.ensemble import RandomForestRegressor
from pyre_extensions import assert_is_instance


class RandomForestGenerationNode(ExternalGenerationNode):
    """A generation node that uses the RandomForestRegressor
    from sklearn to predict candidate performance and picks the
    next point as the random sample that has the best prediction.

    To leverage external methods for candidate generation, the user must
    create a subclass that implements ``update_generator_state`` and
    ``get_next_candidate`` methods. This can then be provided
    as a node into a ``GenerationStrategy``, either as standalone or as
    part of a larger generation strategy with other generation nodes,
    e.g., with a Sobol node for initialization.
    """

    def __init__(self, num_samples: int, regressor_options: Dict[str, Any]) -> None:
        """Initialize the generation node.

        Args:
            regressor_options: Options to pass to the random forest regressor.
            num_samples: Number of random samples from the search space
                used during candidate generation. The sample with the best
                prediction is recommended as the next candidate.
        """
        t_init_start = time.monotonic()
        super().__init__(node_name="RandomForest")
        self.num_samples: int = num_samples
        self.regressor: RandomForestRegressor = RandomForestRegressor(
            **regressor_options
        )
        # We will set these later when updating the state.
        # Alternatively, we could have required experiment as an input
        # and extracted them here.
        self.parameters: Optional[List[RangeParameter]] = None
        self.minimize: Optional[bool] = None
        # Recording time spent in initializing the generator. This is
        # used to compute the time spent in candidate generation.
        self.fit_time_since_gen: float = time.monotonic() - t_init_start

    def update_generator_state(self, experiment: Experiment, data: Data) -> None:
        """A method used to update the state of the generator. This includes any
        models, predictors or any other custom state used by the generation node.
        This method will be called with the up-to-date experiment and data before
        ``get_next_candidate`` is called to generate the next trial(s). Note
        that ``get_next_candidate`` may be called multiple times (to generate
        multiple candidates) after a call to  ``update_generator_state``.

        For this example, we will train the regressor using the latest data from
        the experiment.

        Args:
            experiment: The ``Experiment`` object representing the current state of the
                experiment. The key properties includes ``trials``, ``search_space``,
                and ``optimization_config``. The data is provided as a separate arg.
            data: The data / metrics collected on the experiment so far.
        """
        search_space = experiment.search_space
        parameter_names = list(search_space.parameters.keys())
        metric_names = list(experiment.optimization_config.metrics.keys())
        if any(
            not isinstance(p, RangeParameter) for p in search_space.parameters.values()
        ):
            raise NotImplementedError(
                "This example only supports RangeParameters in the search space."
            )
        if search_space.parameter_constraints:
            raise NotImplementedError(
                "This example does not support parameter constraints."
            )
        if len(metric_names) != 1:
            raise NotImplementedError(
                "This example only supports single-objective optimization."
            )
        # Get the data for the completed trials.
        num_completed_trials = len(experiment.trials_by_status[TrialStatus.COMPLETED])
        x = np.zeros([num_completed_trials, len(parameter_names)])
        y = np.zeros([num_completed_trials, 1])
        for t_idx, trial in experiment.trials.items():
            if trial.status == "COMPLETED":
                trial_parameters = trial.arm.parameters
                x[t_idx, :] = np.array([trial_parameters[p] for p in parameter_names])
                trial_df = data.df[data.df["trial_index"] == t_idx]
                y[t_idx, 0] = trial_df[trial_df["metric_name"] == metric_names[0]][
                    "mean"
                ].item()

        # Train the regressor.
        self.regressor.fit(x, y)
        # Update the attributes not set in __init__.
        self.parameters = search_space.parameters
        self.minimize = experiment.optimization_config.objective.minimize

    def get_next_candidate(
        self, pending_parameters: List[TParameterization]
    ) -> TParameterization:
        """Get the parameters for the next candidate configuration to evaluate.

        We will draw ``self.num_samples`` random samples from the search space
        and predict the objective value for each sample. We will then return
        the sample with the best predicted value.

        Args:
            pending_parameters: A list of parameters of the candidates pending
                evaluation. This is often used to avoid generating duplicate candidates.
                We ignore this here for simplicity.

        Returns:
            A dictionary mapping parameter names to parameter values for the next
            candidate suggested by the method.
        """
        bounds = np.array([[p.lower, p.upper] for p in self.parameters.values()])
        unit_samples = np.random.random_sample([self.num_samples, len(bounds)])
        samples = bounds[:, 0] + (bounds[:, 1] - bounds[:, 0]) * unit_samples
        # Predict the objective value for each sample.
        y_pred = self.regressor.predict(samples)
        # Find the best sample.
        best_idx = np.argmin(y_pred) if self.minimize else np.argmax(y_pred)
        best_sample = samples[best_idx, :]
        # Convert the sample to a parameterization.
        candidate = {
            p_name: best_sample[i].item()
            for i, p_name in enumerate(self.parameters.keys())
        }
        return candidate

## Construct the GenerationStrategy

We will use Sobol for the first 5 trials and defer to random forest for the rest.

In [2]:
generation_strategy = GenerationStrategy(
    name="Sobol+RandomForest",
    nodes=[
        GenerationNode(
            node_name="Sobol",
            model_specs=[ModelSpec(Models.SOBOL)],
            transition_criteria=[
                MaxTrials(
                    # This specifies the maximum number of trials to generate from this node, 
                    # and the next node in the strategy.
                    threshold=5,
                    block_transition_if_unmet=True,
                    transition_to="RandomForest"
                )
            ],
        ),
        RandomForestGenerationNode(num_samples=128, regressor_options={}),
    ],
)

## Run a simple experiment using AxClient

More details on how to use AxClient can be found in the [tutorial](https://ax.dev/tutorials/gpei_hartmann_service.html).

In [3]:
ax_client = AxClient(generation_strategy=generation_strategy)

ax_client.create_experiment(
    name="hartmann_test_experiment",
    parameters=[
        {
            "name": f"x{i}",
            "type": "range",
            "bounds": [0.0, 1.0],
            "value_type": "float",  # Optional, defaults to inference from type of "bounds".
        }
        for i in range(1, 7)
    ],
    objectives={"hartmann6": ObjectiveProperties(minimize=True)},
)


def evaluate(parameterization: TParameterization) -> Dict[str, Tuple[float, float]]:
    x = np.array([parameterization.get(f"x{i+1}") for i in range(6)])
    return {"hartmann6": (assert_is_instance(hartmann6(x), float), 0.0)}

[INFO 01-31 07:12:48] ax.service.ax_client: Starting optimization with verbose logging. To disable logging, set the `verbose_logging` argument to `False`. Note that float values in the logs are rounded to 6 decimal points.


[INFO 01-31 07:12:48] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='x1', parameter_type=FLOAT, range=[0.0, 1.0]), RangeParameter(name='x2', parameter_type=FLOAT, range=[0.0, 1.0]), RangeParameter(name='x3', parameter_type=FLOAT, range=[0.0, 1.0]), RangeParameter(name='x4', parameter_type=FLOAT, range=[0.0, 1.0]), RangeParameter(name='x5', parameter_type=FLOAT, range=[0.0, 1.0]), RangeParameter(name='x6', parameter_type=FLOAT, range=[0.0, 1.0])], parameter_constraints=[]).


### Run the optimization loop

In [4]:
for i in range(15):
    parameterization, trial_index = ax_client.get_next_trial()
    ax_client.complete_trial(
        trial_index=trial_index, raw_data=evaluate(parameterization)
    )

/tmp/tmp.8SPGnWMU26/Ax-main/ax/modelbridge/cross_validation.py:439: UserWarning: Encountered exception in computing model fit quality: RandomModelBridge does not support prediction.
  warn("Encountered exception in computing model fit quality: " + str(e))
[INFO 01-31 07:12:48] ax.service.ax_client: Generated new trial 0 with parameters {'x1': 0.408129, 'x2': 0.57849, 'x3': 0.0297, 'x4': 0.741332, 'x5': 0.92174, 'x6': 0.268424} using model Sobol.


[INFO 01-31 07:12:48] ax.service.ax_client: Completed trial 0 with data: {'hartmann6': (-0.496231, 0.0)}.


/tmp/tmp.8SPGnWMU26/Ax-main/ax/modelbridge/cross_validation.py:439: UserWarning: Encountered exception in computing model fit quality: RandomModelBridge does not support prediction.
  warn("Encountered exception in computing model fit quality: " + str(e))
[INFO 01-31 07:12:48] ax.service.ax_client: Generated new trial 1 with parameters {'x1': 0.798194, 'x2': 0.206233, 'x3': 0.733353, 'x4': 0.45291, 'x5': 0.00771, 'x6': 0.713725} using model Sobol.


[INFO 01-31 07:12:48] ax.service.ax_client: Completed trial 1 with data: {'hartmann6': (-0.345269, 0.0)}.


/tmp/tmp.8SPGnWMU26/Ax-main/ax/modelbridge/cross_validation.py:439: UserWarning: Encountered exception in computing model fit quality: RandomModelBridge does not support prediction.
  warn("Encountered exception in computing model fit quality: " + str(e))
[INFO 01-31 07:12:48] ax.service.ax_client: Generated new trial 2 with parameters {'x1': 0.599229, 'x2': 0.821358, 'x3': 0.481056, 'x4': 0.770153, 'x5': 0.37406, 'x6': 0.861753} using model Sobol.


...

/opt/hostedtoolcache/Python/3.10.16/x64/lib/python3.10/site-packages/sklearn/base.py:1389: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)


[INFO 01-31 07:12:49] ax.service.ax_client: Generated new trial 13 with parameters {'x1': 0.547556, 'x2': 0.23767, 'x3': 0.018173, 'x4': 0.432419, 'x5': 0.176419, 'x6': 0.353044} using model RandomForest.


[INFO 01-31 07:12:49] ax.service.ax_client: Completed trial 13 with data: {'hartmann6': (-0.522496, 0.0)}.


/opt/hostedtoolcache/Python/3.10.16/x64/lib/python3.10/site-packages/sklearn/base.py:1389: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)
[INFO 01-31 07:12:49] ax.service.ax_client: Generated new trial 14 with parameters {'x1': 0.513783, 'x2': 0.112981, 'x3': 0.104419, 'x4': 0.883902, 'x5': 0.472816, 'x6': 0.366435} using model RandomForest.


[INFO 01-31 07:12:49] ax.service.ax_client: Completed trial 14 with data: {'hartmann6': (-0.020736, 0.0)}.


### View the trials generated during optimization

In [5]:
exp_df = exp_to_df(ax_client.experiment)
exp_df

trial_index arm_name trial_status generation_method  hartmann6        x1  \
0             0      0_0    COMPLETED             Sobol  -0.496231  0.408129   
1             1      1_0    COMPLETED             Sobol  -0.345269  0.798194   
2             2      2_0    COMPLETED             Sobol  -0.039492  0.599229   
3             3      3_0    COMPLETED             Sobol  -0.107451  0.239416   
4             4      4_0    COMPLETED             Sobol  -0.206089  0.124417   
5             5      5_0    COMPLETED      RandomForest  -0.004364  0.060960   
6             6      6_0    COMPLETED      RandomForest  -0.034974  0.083282   
7             7      7_0    COMPLETED      RandomForest  -0.016267  0.752962   
8             8      8_0    COMPLETED      RandomForest  -0.839666  0.938778   
9             9      9_0    COMPLETED      RandomForest  -0.106246  0.044084   
10           10     10_0    COMPLETED      RandomForest  -0.002264  0.841064   
11           11     11_0    COMPLETED      RandomForest  -0.255820  0.121119   
12           12     12_0    COMPLETED      RandomForest  -0.019138  0.574683   
13           13     13_0    COMPLETED      RandomForest  -0.522496  0.547556   
14           14     14_0    COMPLETED      RandomForest  -0.020736  0.513783   

          x2        x3        x4        x5        x6  
0   0.578490  0.029700  0.741332  0.921740  0.268424  
1   0.206233  0.733353  0.452910  0.007710  0.713725  
2   0.821358  0.481056  0.770153  0.374060  0.861753  
3   0.447645  0.777358  0.043438  0.710144  0.182038  
4   0.921863  0.595632  0.180080  0.572604  0.479884  
5   0.957160  0.132677  0.877324  0.177332  0.871865  
6   0.419696  0.538598  0.922192  0.309467  0.123649  
7   0.931430  0.732011  0.852249  0.171133  0.480651  
8   0.555577  0.929968  0.310269  0.074154  0.983418  
9   0.856422  0.268863  0.594373  0.171491  0.845881  
10  0.123623  0.028664  0.644466  0.797655  0.917488  
11  0.687474  0.643551  0.388690  0.809305  0.590182  
12  0.689344  0.259461  0.453048  0.779947  0.730395  
13  0.237670  0.018173  0.432419  0.176419  0.353044  
14  0.112981  0.104419  0.883902  0.472816  0.366435

In [6]:
plot_objective_value_vs_trial_index(
    exp_df=exp_df,
    metric_colname="hartmann6",
    minimize=True,
    title="Hartmann6 Objective Value vs. Trial Index",
)

/tmp/tmp.8SPGnWMU26/Ax-main/ax/plot/trace.py:870: FutureWarning:

DataFrame.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.

